# Magnitudenbestimmung

In dieser Übung können Sie ausprobieren, wie man mit Hilfe von Obspy Magnituden bestimmen kann. Zuerst müssen Sie sich einige Obspy Routinen laden und einen Server anwählen. Außerdem muss das Erdbeben bereits lokalisiert sein, denn Sie brauchen die Herdzeit und die Ereigniskoordinaten.

In [1]:
from obspy.core import UTCDateTime, Stream
from obspy.core.util.geodetics import gps2DistAzimuth
from obspy.fdsn import Client
from math import log10
from numpy import median

client = Client()
t = UTCDateTime("2009-04-07T17:47:38")
evlat = 42.3171
evlon = 13.4741

Nun erstellen Sie sich ein Inventory über die verfügbaren Daten zu diesem Ereignis auf dem Server und laden sich die gewünschten Daten herunter. Dabei laden Sie gleichzeitig die Stationsinformationen mit dem Zusatz attach_response=True
Sie können auch das inventory vorher "erforschen".

In [ ]:
inventory = client.get_stations(channel="*", starttime=t, network="MN")
#print inventory
#net = inventory[0]
#print net
#sta = net[0]
#print sta

In [6]:
st = Stream()
for net in inventory:
    for sta in net:
        try:
            st += client.get_waveforms(net.code, sta.code, "*", "BH*", t, t + 1200, attach_response=True)
        except:
            continue
        

#print st 
#print(st.__str__(extended=True))
st.merge(method=1, fill_value='interpolate')
st.detrend   
for tr in st.select(location="10"):
    st.remove(tr)

Als nächstes müssen Sie die Gerätecharakteristik von den Daten abziehen (die Daten restituieren) und ein Wood-Anderson Seismometer simulieren. Dann können Sie die Amplituden auf jeder Spur bestimmen.
Um dann die Magnitude zu berechnen, brauchen Sie noch die Entfernung der Station in Kilometer. Am Ende wird der Median/Mittelwert aus allen bestimmten Magnituden gebildet.

In [7]:
# Gerätecharakteristik des Wood-Anderson-Seismometers:
paz_wa = {'sensitivity': 2800, 'zeros': [0j], 'gain': 1,
          'poles': [-6.2832-4.7124j, -6.2832+4.7124j]}

# Abziehen der Gerätecharakterisitk, simulieren mit WA
st.remove_response(water_level=10)
st.simulate(paz_simulate=paz_wa)

45 Trace(s) in Stream:

MN.TIR..BHN | 2009-04-07T17:56:24.184999Z - 2009-04-07T18:07:35.584999Z | 20.0 Hz, 13429 samples
...
(43 other traces)
...
MN.BNI..BHN | 2009-04-07T17:47:38.017863Z - 2009-04-07T18:07:37.967863Z | 20.0 Hz, 24000 samples

[Use "print(Stream.__str__(extended=True))" to print all Traces]

In [12]:
# leere Liste, in die später alle Magnitudenwerte der einzelnen Spuren geschrieben werden
mags = []

stations = client.get_stations(t, t + 1200, network="MN")

# Schleife über alle Spuren
for tr in st:
    station = tr.stats.station
    for N in stations:
        for stat in N:
            if station == stat.code:
                sta_lat = stat.latitude
                sta_lon = stat.longitude

    # max. Amplitude der Spur bestimmen
    ampl = max(abs(tr.data))
    #print ampl
    # Stationsentfernung berechnen
    print sta_lat, sta_lon
    epi_dist, az, baz = gps2DistAzimuth(evlat, evlon, sta_lat, sta_lon)
    print "Dist, Az, Baz:", epi_dist, az, baz
    # Berechnen der Magnitude
    ml = log10(ampl) + 1.11 * log10(epi_dist) + 0.00189 * epi_dist - 2.09
    print station, ml
    mags.append(ml)
# autom. Ende der Schleife

net_mag = median(mags)
print "Network magnitude:", net_mag

41.3472 19.8631
Dist, Az, Baz: 541404.11762 99.3304848092 283.594247087
TIR 1024.2424065
41.3472 19.8631
Dist, Az, Baz: 541404.11762 99.3304848092 283.594247087
TIR 1024.25444674
41.3472 19.8631
Dist, Az, Baz: 541404.11762 99.3304848092 283.594247087
TIR 1024.13492155
39.1794 16.7583
Dist, Az, Baz: 445275.216673 140.395902447 322.540764127
TIP 843.503695356
46.47223 9.34732
Dist, Az, Baz: 566639.484568 325.972508812 143.082884193
TUE 1073.15007305
35.8373 14.5242
Dist, Az, Baz: 725067.40368 172.465383206 353.128405305
WDD 1371.46140871
45.709 13.764
Dist, Az, Baz: 377597.993452 3.42936383112 183.630881486
TRI 716.028796057
42.618 23.235
Dist, Az, Baz: 803000.62701 84.3219776113 270.921004739
VTS 1519.39172287
46.47223 9.34732
Dist, Az, Baz: 566639.484568 325.972508812 143.082884193
TUE 1073.1162763
46.47223 9.34732
Dist, Az, Baz: 566639.484568 325.972508812 143.082884193
TUE 1073.0706234
35.8373 14.5242
Dist, Az, Baz: 725067.40368 172.465383206 353.128405305
WDD 1371.39184398
42.618 23